# Описание проекта 

**Компании «ГлавРосГосНефть» нужно решить, где бурить новую скважину.**  
Для выбора локакии:  
- В избранном регионе соберём характеристики для скважин: качество нефти и объём её запасов
- Построим модель для предсказания объёма запасов в новых скважинах
- Выберем скважины с самыми высокими оценками значений
- Определим регион с максимальной суммарной прибылью отобранных скважин

## Описание данных

- id — уникальный идентификатор скважины
- f0, f1, f2 — три признака точек
- product (целевой признак) — объём запасов в скважине (тыс. баррелей) 


## Загрузка данных

In [1]:
import warnings

warnings.filterwarnings('ignore')

In [2]:
!pip install --upgrade pip -q

In [3]:
!pip install --upgrade Pillow -q

In [4]:
!pip install -U scikit-learn -q

In [5]:
!pip install ydata-profiling -q

In [6]:
# библиотеки
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from scipy import stats as st
import numpy as np

from IPython.display import display, HTML

from sklearn.preprocessing import StandardScaler

from sklearn.metrics import accuracy_score


from sklearn.metrics import root_mean_squared_error

from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LinearRegression

from ydata_profiling import ProfileReport

In [7]:
# данные
data_1 = pd.read_csv("https://code.s3.yandex.net/datasets/geo_data_0.csv")
data_2 = pd.read_csv("https://code.s3.yandex.net/datasets/geo_data_1.csv")
data_3 = pd.read_csv("https://code.s3.yandex.net/datasets/geo_data_2.csv")

## Предобработка данных

### data_1

In [8]:
data_1.head(3)

id        f0        f1        f2     product
0  txEyH  0.705745 -0.497823  1.221170  105.280062
1  2acmU  1.334711 -0.340164  4.365080   73.037750
2  409Wp  1.022732  0.151990  1.419926   85.265647

In [9]:
data_1.shape

(100000, 5)

In [10]:
data_1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 5 columns):
 #   Column   Non-Null Count   Dtype  
---  ------   --------------   -----  
 0   id       100000 non-null  object 
 1   f0       100000 non-null  float64
 2   f1       100000 non-null  float64
 3   f2       100000 non-null  float64
 4   product  100000 non-null  float64
dtypes: float64(4), object(1)
memory usage: 3.8+ MB


In [11]:
data_1.duplicated().sum()

0

In [12]:
data_1.isna().sum()

id         0
f0         0
f1         0
f2         0
product    0
dtype: int64

**С данными всё в порядке, пропуски и дубликаты отсутствуют**

In [13]:
num = ['f0', 'f1', 'f2']
data_1[num].corr()

f0        f1        f2
f0  1.000000 -0.440723 -0.003153
f1 -0.440723  1.000000  0.001724
f2 -0.003153  0.001724  1.000000

In [14]:
profile = ProfileReport(data_1, title="Report 1")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**отделим целевой признак "product"**

In [15]:
X_1 = data_1.drop(['id', 'product'], axis = 1)
y_1 = data_1['product']

### вывод

- С данными всё в порядке, пропуски и дубликаты отсутствуют
- максимальное знаачение запасов = 185.36435 тыс.баррелей
- найдена всего одна пустая скважина
- наибольшая зависимость у признака f2 объёма запасов = 0.486

## data_2

In [16]:
data_2.head(3)

id         f0        f1        f2     product
0  kBEdx -15.001348 -8.276000 -0.005876    3.179103
1  62mP7  14.272088 -3.475083  0.999183   26.953261
2  vyE1P   6.263187 -5.948386  5.001160  134.766305

In [17]:
data_2.shape

(100000, 5)

In [18]:
data_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 5 columns):
 #   Column   Non-Null Count   Dtype  
---  ------   --------------   -----  
 0   id       100000 non-null  object 
 1   f0       100000 non-null  float64
 2   f1       100000 non-null  float64
 3   f2       100000 non-null  float64
 4   product  100000 non-null  float64
dtypes: float64(4), object(1)
memory usage: 3.8+ MB


In [19]:
data_2.duplicated().sum()

0

In [20]:
data_2.isna().sum()

id         0
f0         0
f1         0
f2         0
product    0
dtype: int64

**С данными всё в порядке, пропуски и дубликаты отсутствуют**

In [21]:
data_2[num].corr()

f0        f1        f2
f0  1.000000  0.182287 -0.001777
f1  0.182287  1.000000 -0.002595
f2 -0.001777 -0.002595  1.000000

**отделим целевой признак "product"**

In [22]:
profile = ProfileReport(data_2, title="Report 2")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [23]:
X_2 = data_2.drop(['id', 'product'], axis = 1)
y_2 = data_2['product']

### вывод

- С данными всё в порядке, пропуски и дубликаты отсутствуют
- максимальное знаачение запасов = 137.94541 тыс.баррелей
- пустые скважины составляют 8.2% от общего кол-ва
- наибольшая зависимость у признака f2 и объёма запасов = 0.976 => корреляция слишком высокая => есть подозрения на утечку целевого признака -> нужно обсудить это с заказчиком

## data_3

In [24]:
data_3.head(3)

id        f0        f1        f2    product
0  fwXo0 -1.146987  0.963328 -0.828965  27.758673
1  WJtFt  0.262778  0.269839 -2.530187  56.069697
2  ovLUW  0.194587  0.289035 -5.586433  62.871910

In [25]:
data_3.shape

(100000, 5)

In [26]:
data_3.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 5 columns):
 #   Column   Non-Null Count   Dtype  
---  ------   --------------   -----  
 0   id       100000 non-null  object 
 1   f0       100000 non-null  float64
 2   f1       100000 non-null  float64
 3   f2       100000 non-null  float64
 4   product  100000 non-null  float64
dtypes: float64(4), object(1)
memory usage: 3.8+ MB


In [27]:
data_3.duplicated().sum()

0

In [28]:
data_3.isna().sum()

id         0
f0         0
f1         0
f2         0
product    0
dtype: int64

**С данными всё в порядке, пропуски и дубликаты отсутствуют**

In [29]:
data_3[num].corr()

f0        f1        f2
f0  1.000000  0.000528 -0.000448
f1  0.000528  1.000000  0.000779
f2 -0.000448  0.000779  1.000000

In [30]:
profile = ProfileReport(data_3, title="Report 3")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**отделим целевой признак "product"**

In [31]:
X_3 = data_3.drop(['id', 'product'], axis = 1)
y_3 = data_3['product']

### вывод

- С данными всё в порядке, пропуски и дубликаты отсутствуют
- максимальное знаачение запасов = 190.02984 тыс.баррелей
- найдена всего 1 пустая скважина
- наибольшая зависимость у признака f2 и объёма запасов = 0.448

## Обучение моделей

### Регион 1

In [32]:
# создадим функцию для: масштабирования данных
# обучения модели
# предсказаниий

def compil(X, y):
    X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.25, random_state=42)
    scaler = StandardScaler()

    X_train_scaled = scaler.fit_transform(X_train)
    X_valid_scaled = scaler.transform(X_valid)
    model = LinearRegression()
    model.fit(X_train_scaled, y_train)
    pred = pd.Series(model.predict(X_valid_scaled))
    return model, pred, y_train, y_valid

In [33]:
model_1, pred_1, y_train_1, y_valid_1 = compil(X_1, y_1)

### Регион 2

In [34]:
model_2, pred_2, y_train_2, y_valid_2 = compil(X_2, y_2)

### Регион 3

In [35]:
model_3, pred_3, y_train_3, y_valid_3 = compil(X_3, y_3)

### Средний запас предсказанного сырья и RMSE моделей

In [36]:
# средние значения предсказанных объёмов по регионам
mean_1 = pred_1.mean()
mean_2 = pred_2.mean()
mean_3 = pred_3.mean()

In [37]:
# rmse моделей
rmse_1 = root_mean_squared_error(y_valid_1, pred_1)
rmse_2 = root_mean_squared_error(y_valid_2, pred_2)
rmse_3 = root_mean_squared_error(y_valid_3, pred_3)

In [38]:
display(HTML('<b>Регион №1:</b>'))
print(f'RMSE: {rmse_1} \npredicted mean: {mean_1}\nreal mean: {y_valid_1.mean()}')

display(HTML('<b>Регион №2:</b>'))
print(f'RMSE: {rmse_2} \nmean: {mean_2}\nreal mean: {y_valid_2.mean()}')

display(HTML('<b>Регион №3:</b>'))
print(f'RMSE: {rmse_3} \nmean: {mean_3}\nreal mean: {y_valid_3.mean()}')

RMSE: 37.756600350261685 
predicted mean: 92.39879990657768
real mean: 92.32595637084387


RMSE: 0.8902801001028815 
mean: 68.7128780391376
real mean: 68.72538074722745


RMSE: 40.145872311342174 
mean: 94.77102387765936
real mean: 95.15099907171961


<b> истинное и предсказанные значения средних очень близки

## Расчёт прибыли

- <b> При нынешних ценах один баррель сырья приносит 450 рублей дохода. Доход с каждой единицы продукта составляет 450 тыс. рублей, поскольку объём указан в тысячах баррелей.
- <b> Бюджет на разработку скважин в регионе — 10 млрд рублей.
- <b> В итоге будет выбрано 200 точек

In [39]:
# запишем все значения в переменные
# бюджет на регион
TOTAL_BUDGET = 10**10
# кол-во скважин
TOTAL_WELLS = 200
# доход с каждой единицы продукта
BARREL_PRICE = 450000

### рассчитаем сколько примерно потратят на 1 скважину     

In [40]:
# потратят на 1 скважину
ONE_WELL_PRICE = TOTAL_BUDGET / TOTAL_WELLS
print(f'{ONE_WELL_PRICE} руб.')

50000000.0 руб.


<b> найдём нужный объём запасов в скважине 

In [41]:
MIN_VOLUME = ONE_WELL_PRICE / BARREL_PRICE
print('X =', round(MIN_VOLUME, 3))

X = 111.111


<b> т.е. достаточный объём сырья для безубыточной разработки новой скважины равен = 111.111 тыс. баррелей

<b> также заметили, что средние значения запасов скважин по регионам прилично ниже минимальных для безубыточной разработки

In [42]:
# напишем функцию для отбора безубыточных скважин
def check(pred):
    pred = pred.where(pred > MIN_VOLUME).dropna()
    print(f'Удалось найти {pred.shape[0]} безубыточных скважин')
    return

In [43]:
# проверим предсказания по регионам
check(pred_1)
check(pred_2)
check(pred_3)

Удалось найти 5258 безубыточных скважин
Удалось найти 4520 безубыточных скважин
Удалось найти 5239 безубыточных скважин


## Функция для расчёта прибыли по выбранным скважинам и предсказаниям модели

* <b> отберём 200 лучших точек предсказанных моделью и просуммируем целевое значение объёма сырья,       
соответствующее этим предсказаниям, чтобы вычислить прибыль

In [44]:
# функция для расчёта прибыли
def profit(true, pred):
    pred = pred.sort_values(ascending=False)
    true = true[pred.index][:TOTAL_WELLS]*BARREL_PRICE
    return round((true.sum() - TOTAL_BUDGET), 3)

In [45]:
# обновляем индексы
y_valid_1 = y_valid_1.reset_index(drop=True)
y_valid_2 = y_valid_2.reset_index(drop=True)
y_valid_3 = y_valid_3.reset_index(drop=True)

In [46]:
print(f'Прибыль первого региона {profit(y_valid_1, pred_1)} руб')
print(f'Прибыль второго региона {profit(y_valid_2, pred_2)} руб')
print(f'Прибыль третьего региона {profit(y_valid_3, pred_3)} руб')

Прибыль первого региона 3359141114.462 руб
Прибыль второго региона 2415086696.682 руб
Прибыль третьего региона 2598571759.374 руб


### вывод

- самый прибыльный регион номер 1: 3.36 млрд. руб
- на втором месте регион номер 3: 2.6 млрд. руб
- на третьем месте регион номер 2: 2.42 млрд. руб

## Риски и прибыль для каждого региона

In [47]:
# n = 500 т.к. изначально изучают 500 скважин
def func(true, pred):
    state = np.random.RandomState(12345)
    values = []
    for i in range(1000):
        pred_subsample = pred.sample(n = 500, replace = True, random_state = state)
        true_subsample = true[pred_subsample.index]
        values.append(profit(true_subsample, pred_subsample))
                      
    values = pd.Series(values)
    return values

In [48]:
values_1 = func(y_valid_1, pred_1)
values_2 = func(y_valid_2, pred_2)
values_3 = func(y_valid_3, pred_3)

In [49]:
print(f'Средняя прибыль первого региона: {round(values_1.mean(), 3)}')
print(f'Средняя прибыль второго региона: {round(values_2.mean(), 3)}')
print(f'Средняя прибыль третьего региона: {round(values_3.mean(), 3)}')

Средняя прибыль первого региона: 435933772.139
Средняя прибыль второго региона: 489661254.412
Средняя прибыль третьего региона: 403687927.862


<b> во втором регионе наибольшая средняя прибыль

In [50]:
def trust(values, num):
    print(f'Регион {num}')
    print(f'Нижняя граница доверительного интервала прибыли: {round(values.quantile(0.025), 3)}')
    print(f'Верхняя граница доверительного интервала прибыли: {round(values.quantile(0.975), 3)}')
    count = 0
    for i in values:
        if i < 0:
            count += 1
    print(f'Доля убытков: {count/len(values)}%') 
    print()
    return

In [51]:
trust(values_1, 1)
trust(values_2, 2)
trust(values_3, 3)

Регион 1
Нижняя граница доверительного интервала прибыли: -116231612.777
Верхняя граница доверительного интервала прибыли: 966504180.708
Доля убытков: 0.061%

Регион 2
Нижняя граница доверительного интервала прибыли: 55116177.274
Верхняя граница доверительного интервала прибыли: 905762650.425
Доля убытков: 0.011%

Регион 3
Нижняя граница доверительного интервала прибыли: -153116984.762
Верхняя граница доверительного интервала прибыли: 952887416.708
Доля убытков: 0.071%



<b> во всех регионах риск убытков менее 2.5%, значит будем сравнивать по средней прибыли. Наиболее прибыльный регион номер 2. Стоит выбрать его для разработки. Также у него самый надёжный полностью положительный 95% доверительный интервал.

## Вывод

- проверили качество данных: пропуски и дубликаты отсутвуют
- во втором регионе заметиои слишком сильную зависимость признака 'f2' и целевого из-за чего предположили об его утечке 
- проверили средние значение запасов скаважин по регионам и они оказались меньше минимального для безубыточной разработки
- также выяснили, что все регионы оказались прибыльными
- во всех регионах риск убытков менее 2.5%, значит будем сравнивать по средней прибыли. **Наиболее прибыльный регион номер 2.** Стоит выбрать его для разработки. Также у него самый надёжный полностью положительный 95% доверительный интервал.